In [1]:
import sys, os
lib_path = os.path.abspath(os.path.join('..'))
sys.path.append(lib_path)
import tensorflow as tf
import csv
import numpy as np
import tflib as lib
import tflib.ops.linear
import tflib.ops.conv1d
#import language_helpers
import time
from sklearn.utils import shuffle

In [2]:
score_t = []
how_win_t = []
with open('../data/generate_data_ave.txt') as f:
    file = f.readlines()
    for data in file:
        s = data.split()
        score_one = s[0]
        how_win_one = s[1]
        scores = score_one.split('-')
        score1 = round(float(scores[0]),1)
        score2 = round(float(scores[1]),1)
        score_t.append((score1, score2))
        how_win_t.append(how_win_one)

print(len(score_t))

10100


In [3]:
score_t, how_win_t = shuffle(score_t, how_win_t)
t_len = len(score_t)
score = score_t[0:int(t_len*0.8)]
score_test = score_t[int(t_len*0.8):]
how_win = how_win_t[0:int(t_len*0.8)]
how_win_test = how_win_t[int(t_len*0.8):]

In [4]:
"""
team = []
score_t = []
how_win_t = []
sentence = []
with open('../data_set.csv') as f:
    f_csv = csv.reader(f)
    headers = next(f_csv)
    for row in f_csv:
        teams = row[0].split('_')
        team.append((teams[0], teams[1]))
        scores = row[1].split('-')
        score_t.append((int(scores[0]), int(scores[1])))
        how_win_t.append(row[2])
        sentence.append(row[3])
        
t_len = len(score_t)
score = score_t[0:int(t_len*0.8)]
score_test = score_t[int(t_len*0.8):]
how_win = how_win_t[0:int(t_len*0.8)]
how_win_test = how_win_t[int(t_len*0.8):]


"""

"\nteam = []\nscore_t = []\nhow_win_t = []\nsentence = []\nwith open('../data_set.csv') as f:\n    f_csv = csv.reader(f)\n    headers = next(f_csv)\n    for row in f_csv:\n        teams = row[0].split('_')\n        team.append((teams[0], teams[1]))\n        scores = row[1].split('-')\n        score_t.append((int(scores[0]), int(scores[1])))\n        how_win_t.append(row[2])\n        sentence.append(row[3])\n        \nt_len = len(score_t)\nscore = score_t[0:int(t_len*0.8)]\nscore_test = score_t[int(t_len*0.8):]\nhow_win = how_win_t[0:int(t_len*0.8)]\nhow_win_test = how_win_t[int(t_len*0.8):]\n\n\n"

In [5]:
#for i in range(len(score)):
#    print(score[i], how_win[i])

In [6]:
BATCH_SIZE = 64
SEQ_LEN = 2
SCORE_DIM = 20  #generator score dimention
DIM = 128
LAMBDA = 10 # Gradient penalty lambda hyperparameter.
ITERS = 5000
CRITIC_ITERS = 10
NOIZE_DIM = 10

In [7]:
inv_charmap = []
inv_charmap.append('unk')
charmap = {'unk':0}
for word in how_win:
    if word not in inv_charmap:
        charmap[word] = len(inv_charmap)
        inv_charmap.append(word)

In [8]:
inv_charmap

['unk', '大败', '惜败', '大胜', '轻取', '不敌', '击败', '险胜', '痛宰', '战胜', '掀翻']

In [9]:
def get_next_batch(batch_size, _score, _how_win, index):
    length = len(score)
    start_point = index * batch_size
    batch_gen_score = []
    batch_disc_score = []
    batch_how_win = []
    for i in range(batch_size):
        current_point = start_point + i
        if current_point >= length:
            current_point -= length
        
        one_score = _score[current_point]
        gen_score = [one_score[0]/200.0 for i in range(int(SCORE_DIM/2))] + [one_score[1]/200.0 for i in range(int(SCORE_DIM/2))]
        batch_gen_score.append(gen_score)
        
        disc_score = [[one_score[0]/200.0 for i in range(len(charmap))]] + [[one_score[1]/200.0 for i in range(len(charmap))]]
        batch_disc_score.append(disc_score)
        
        batch_how_win.append([charmap[_how_win[current_point]],0])

    
    return batch_gen_score, batch_disc_score, batch_how_win

In [10]:
def softmax(logits):
    return tf.reshape(
        tf.nn.softmax(
            tf.reshape(logits, [-1, len(charmap)])
        ),
        tf.shape(logits)
    )
def make_noise(shape):
    return tf.random_normal(shape)

def ResBlock(name, inputs): 
    output = inputs
    output = tf.nn.relu(output)
    output = lib.ops.conv1d.Conv1D(name+'.1', DIM, DIM, 5, output)
    output = tf.nn.relu(output)
    #output = tf.expand_dims(output, 2)
    #print(output)
    output = lib.ops.conv1d.Conv1D(name+'.2', DIM, DIM, 5, output)
    #output = tf.expand_dims(output, 2)
    return inputs + (0.3*output)

In [11]:
def Generator(n_samples, scores, prev_outputs=None):
    output = make_noise(shape=[n_samples, NOIZE_DIM])
    output = tf.concat([scores, output], 1)
    output = lib.ops.linear.Linear('Generator.Input', SCORE_DIM+NOIZE_DIM, SEQ_LEN*DIM, output)
    output = tf.reshape(output, [-1, DIM, SEQ_LEN])
    output = ResBlock('Generator.1', output)
    output = ResBlock('Generator.2', output)
    output = ResBlock('Generator.3', output)
    output = ResBlock('Generator.4', output)
    output = ResBlock('Generator.5', output)
    output = lib.ops.conv1d.Conv1D('Generator.Output', DIM, len(charmap), 1, output)
    
    #output = tf.expand_dims(output, 2)
    output = tf.transpose(output, [0, 2, 1])
    output = softmax(output)
    return output

#test
"""
score = tf.placeholder(tf.float32, shape=[BATCH_SIZE, 20])
Generator(BATCH_SIZE, score)
"""

'\nscore = tf.placeholder(tf.float32, shape=[BATCH_SIZE, 20])\nGenerator(BATCH_SIZE, score)\n'

In [12]:
def Discriminator(inputs, scores):
    output = tf.concat([inputs, scores], 1)
    output = tf.transpose(output, [0,2,1])
    output = lib.ops.conv1d.Conv1D('Discriminator.Input', len(charmap), DIM, 1, output)
    output = ResBlock('Discriminator.1', output)
    output = ResBlock('Discriminator.2', output)
    output = ResBlock('Discriminator.3', output)
    output = ResBlock('Discriminator.4', output)
    output = ResBlock('Discriminator.5', output)
    output = tf.reshape(output, [-1, (2+SEQ_LEN)*DIM])
    output = lib.ops.linear.Linear('Discriminator.Output', (2+SEQ_LEN)*DIM, 1, output)
    return output

#test
"""
real_inputs_discrete = tf.placeholder(tf.int32, shape=[BATCH_SIZE, SEQ_LEN])
real_inputs = tf.one_hot(real_inputs_discrete, len(charmap))
score = tf.placeholder(tf.float32, shape=[BATCH_SIZE, 2, len(charmap)])
Discriminator(real_inputs, score) 
"""

'\nreal_inputs_discrete = tf.placeholder(tf.int32, shape=[BATCH_SIZE, SEQ_LEN])\nreal_inputs = tf.one_hot(real_inputs_discrete, len(charmap))\nscore = tf.placeholder(tf.float32, shape=[BATCH_SIZE, 2, len(charmap)])\nDiscriminator(real_inputs, score) \n'

In [13]:
score_for_gen = tf.placeholder(tf.float32, shape=[None, SCORE_DIM])
score_for_disc = tf.placeholder(tf.float32, shape=[None, 2, len(charmap)])
real_inputs_discrete = tf.placeholder(tf.int32, shape=[None, SEQ_LEN])
real_inputs = tf.one_hot(real_inputs_discrete, len(charmap))
fake_inputs = Generator(BATCH_SIZE, score_for_gen)
fake_inputs_discrete = tf.argmax(fake_inputs, fake_inputs.get_shape().ndims-1)

sample_size = tf.placeholder(tf.int32, shape=[])
sample_inputs = Generator(sample_size, score_for_gen)



disc_real = Discriminator(real_inputs, score_for_disc) 
disc_fake = Discriminator(fake_inputs, score_for_disc)

disc_cost = tf.reduce_mean(disc_fake) - tf.reduce_mean(disc_real)
gen_cost = -tf.reduce_mean(disc_fake)

In [14]:
# WGAN lipschitz-penalty
alpha = tf.random_uniform(
    shape=[BATCH_SIZE,1,1], 
    minval=0.,
    maxval=1.
)
differences = fake_inputs - real_inputs
interpolates = real_inputs + (alpha*differences)
gradients = tf.gradients(Discriminator(interpolates, score_for_disc), [interpolates])[0]
slopes = tf.sqrt(tf.reduce_sum(tf.square(gradients), reduction_indices=[1,2]))
gradient_penalty = tf.reduce_mean((slopes-1.)**2)
disc_cost += LAMBDA*gradient_penalty

tf.summary.scalar('Generator Cost',gen_cost)
tf.summary.scalar('Discriminator Cost',disc_cost)
merged = tf.summary.merge_all()

gen_params = lib.params_with_name('Generator')
disc_params = lib.params_with_name('Discriminator')

gen_train_op = tf.train.AdamOptimizer(learning_rate=1e-4, beta1=0.5, beta2=0.9).minimize(gen_cost, var_list=gen_params)
disc_train_op = tf.train.AdamOptimizer(learning_rate=1e-4, beta1=0.5, beta2=0.9).minimize(disc_cost, var_list=disc_params)

下面的训练结果格式是：

（比分1，比分2）（预测结果，实际结果）

In [15]:
with tf.Session() as session:
    
    summary_writer = tf.summary.FileWriter(logdir='data/')
    session.run(tf.global_variables_initializer())
    sc_gen = None 
    sc_disc = None
    _data = None
    def generate_samples():
        sc_gen, sc_disc, _data = get_next_batch(len(score_test), score_test, how_win_test, 0)
        samples = session.run(sample_inputs, feed_dict={sample_size: len(sc_gen), score_for_gen:sc_gen, score_for_disc:sc_disc})
        samples = np.argmax(samples, axis=2)
        decoded_samples = []
        for i in range(len(samples)):
            decoded_samples.append((inv_charmap[samples[i][0]], inv_charmap[_data[i][0]]))
        return decoded_samples
    
    batch_index = 0
    for iteration in range(ITERS):
        start_time = time.time()
        
        # Train generator
        if iteration > 0:
            _ = session.run(gen_train_op, feed_dict={score_for_gen:sc_gen, score_for_disc:sc_disc})
            
        
         # Train critic
        for i in range(CRITIC_ITERS):
            if batch_index * BATCH_SIZE > len(score):
                batch_index = 0
            sc_gen, sc_disc, _data= get_next_batch(BATCH_SIZE, score, how_win, batch_index)
            batch_index += 1
            _disc_cost, _gen_cost, _gradient_penalty,  _,summary = session.run(
                [disc_cost, gen_cost, gradient_penalty, disc_train_op,merged],
                feed_dict={real_inputs_discrete:_data, score_for_gen:sc_gen, score_for_disc: sc_disc}
            )
            summary_writer.add_summary(summary,iteration+i)
        
        #lib.plot.plot('time', time.time() - start_time)
        #lib.plot.plot('train disc cost', _disc_cost)
        
        #if iteration % 100 == 99:
            #lib.plot.flush()
        
        #lib.plot.tick()
        if iteration % 10 == 0:
            print(iteration, _disc_cost, _gen_cost, _gradient_penalty)
        
        if iteration % 100 == 0:
            sample = generate_samples()
            for i in range(len(sample)):
                print(score_test[i], sample[i])
        
        if iteration % 500 == 0:
            saver = tf.train.Saver()
            saver.save(session, 'models/trained_model',global_step=iteration)
summary_writer.close()

0 -0.287063 0.0563771 0.00286176
(124.0, 120.0) ('战胜', '掀翻')
(114.0, 110.0) ('unk', '险胜')
(128.0, 133.0) ('战胜', '惜败')
(106.0, 74.0) ('险胜', '痛宰')
(120.0, 116.0) ('战胜', '掀翻')
(102.0, 97.0) ('掀翻', '掀翻')
(103.0, 124.0) ('unk', '大败')
(109.0, 97.0) ('unk', '击败')
(106.0, 94.0) ('unk', '战胜')
(123.0, 109.0) ('险胜', '击败')
(124.0, 118.0) ('战胜', '掀翻')
(126.0, 123.0) ('痛宰', '险胜')
(104.0, 82.0) ('轻取', '轻取')
(101.0, 98.0) ('战胜', '掀翻')
(109.0, 99.0) ('险胜', '战胜')
(112.0, 86.0) ('轻取', '大胜')
(100.0, 77.0) ('战胜', '轻取')
(103.0, 99.0) ('unk', '掀翻')
(118.0, 105.0) ('unk', '击败')
(111.0, 85.0) ('险胜', '大胜')
(107.0, 101.0) ('险胜', '掀翻')
(110.0, 119.0) ('险胜', '不敌')
(104.0, 72.0) ('险胜', '痛宰')
(104.0, 69.0) ('不敌', '痛宰')
(127.0, 102.0) ('战胜', '大胜')
(124.0, 89.0) ('痛宰', '痛宰')
(107.0, 79.0) ('痛宰', '大胜')
(107.0, 94.0) ('轻取', '击败')
(102.0, 110.0) ('痛宰', '不敌')
(117.0, 138.0) ('险胜', '大败')
(129.0, 123.0) ('战胜', '险胜')
(109.0, 96.0) ('掀翻', '战胜')
(122.0, 116.0) ('险胜', '掀翻')
(116.0, 102.0) ('unk', '击败')
(126.0, 92.0) ('战胜', '痛宰'

(121.0, 139.0) ('险胜', '大败')
(135.0, 114.0) ('战胜', '轻取')
(123.0, 119.0) ('险胜', '掀翻')
(114.0, 108.0) ('险胜', '掀翻')
(123.0, 89.0) ('战胜', '痛宰')
(123.0, 113.0) ('险胜', '战胜')
(122.0, 143.0) ('轻取', '大败')
(122.0, 100.0) ('unk', '轻取')
(112.0, 120.0) ('击败', '不敌')
(111.0, 129.0) ('险胜', '大败')
(144.0, 146.0) ('险胜', '惜败')
(104.0, 100.0) ('险胜', '险胜')
(110.0, 105.0) ('险胜', '掀翻')
(106.0, 71.0) ('轻取', '痛宰')
(103.0, 122.0) ('险胜', '大败')
(124.0, 144.0) ('险胜', '大败')
(107.0, 117.0) ('战胜', '不敌')
10 -1.20696 0.374367 0.00477814
20 -0.893031 1.02794 0.00655819
30 -0.833136 1.65836 0.00627624
40 -0.765085 2.0066 0.00369571
50 -0.743273 2.34305 0.00362294
60 -0.691674 2.62317 0.00471195
70 -0.697524 2.73075 0.00314148
80 -0.677705 2.81187 0.00395506
90 -0.660403 2.93053 0.00513782
100 -0.685603 3.37364 0.00935386
(124.0, 120.0) ('险胜', '掀翻')
(114.0, 110.0) ('战胜', '险胜')
(128.0, 133.0) ('惜败', '惜败')
(106.0, 74.0) ('战胜', '痛宰')
(120.0, 116.0) ('痛宰', '掀翻')
(102.0, 97.0) ('痛宰', '掀翻')
(103.0, 124.0) ('痛宰', '大败')
(109.0, 97.

(128.0, 148.0) ('险胜', '大败')
(110.0, 112.0) ('轻取', '惜败')
(110.0, 112.0) ('轻取', '惜败')
(122.0, 117.0) ('险胜', '险胜')
(103.0, 121.0) ('战胜', '大败')
(121.0, 141.0) ('险胜', '大败')
(102.0, 123.0) ('险胜', '大败')
(123.0, 90.0) ('痛宰', '痛宰')
(102.0, 110.0) ('战胜', '不敌')
(119.0, 108.0) ('轻取', '击败')
(107.0, 125.0) ('痛宰', '大败')
(106.0, 96.0) ('险胜', '战胜')
(101.0, 67.0) ('险胜', '痛宰')
(103.0, 89.0) ('惜败', '击败')
(104.0, 122.0) ('战胜', '大败')
(105.0, 93.0) ('痛宰', '击败')
(104.0, 91.0) ('战胜', '战胜')
(114.0, 102.0) ('险胜', '战胜')
(113.0, 123.0) ('痛宰', '不敌')
(125.0, 93.0) ('轻取', '痛宰')
(127.0, 115.0) ('惜败', '击败')
(119.0, 98.0) ('痛宰', '轻取')
(109.0, 129.0) ('痛宰', '大败')
(129.0, 97.0) ('惜败', '痛宰')
(116.0, 111.0) ('痛宰', '掀翻')
(112.0, 88.0) ('轻取', '轻取')
(139.0, 111.0) ('险胜', '大胜')
(104.0, 101.0) ('惜败', '险胜')
(103.0, 113.0) ('险胜', '不敌')
(135.0, 106.0) ('惜败', '大胜')
(122.0, 100.0) ('战胜', '轻取')
(114.0, 123.0) ('惜败', '不敌')
(112.0, 90.0) ('险胜', '轻取')
(107.0, 103.0) ('轻取', '险胜')
(107.0, 104.0) ('险胜', '险胜')
(115.0, 110.0) ('惜败', '险胜')
(11

110 -0.622299 3.49863 0.00802217
120 -0.65184 3.93517 0.00496853
130 -0.686409 3.82949 0.00703453
140 -0.729008 3.84112 0.00500463
150 -0.673927 4.13543 0.00594644
160 -0.69028 4.22752 0.00763018
170 -0.727978 4.3764 0.00525529
180 -0.645772 4.44767 0.00734345
190 -0.722552 4.56665 0.00624021
200 -0.726696 4.55428 0.00691678
(124.0, 120.0) ('惜败', '掀翻')
(114.0, 110.0) ('痛宰', '险胜')
(128.0, 133.0) ('掀翻', '惜败')
(106.0, 74.0) ('惜败', '痛宰')
(120.0, 116.0) ('击败', '掀翻')
(102.0, 97.0) ('掀翻', '掀翻')
(103.0, 124.0) ('战胜', '大败')
(109.0, 97.0) ('险胜', '击败')
(106.0, 94.0) ('掀翻', '战胜')
(123.0, 109.0) ('惜败', '击败')
(124.0, 118.0) ('轻取', '掀翻')
(126.0, 123.0) ('掀翻', '险胜')
(104.0, 82.0) ('惜败', '轻取')
(101.0, 98.0) ('掀翻', '掀翻')
(109.0, 99.0) ('轻取', '战胜')
(112.0, 86.0) ('不敌', '大胜')
(100.0, 77.0) ('险胜', '轻取')
(103.0, 99.0) ('惜败', '掀翻')
(118.0, 105.0) ('惜败', '击败')
(111.0, 85.0) ('轻取', '大胜')
(107.0, 101.0) ('战胜', '掀翻')
(110.0, 119.0) ('轻取', '不敌')
(104.0, 72.0) ('不敌', '痛宰')
(104.0, 69.0) ('惜败', '痛宰')
(127.0, 102.0)

(127.0, 131.0) ('战胜', '惜败')
(114.0, 90.0) ('不敌', '轻取')
(119.0, 139.0) ('险胜', '大败')
(119.0, 92.0) ('惜败', '大胜')
(118.0, 123.0) ('险胜', '惜败')
(115.0, 104.0) ('掀翻', '击败')
(111.0, 106.0) ('掀翻', '掀翻')
(127.0, 115.0) ('轻取', '击败')
(111.0, 121.0) ('惜败', '不敌')
(112.0, 108.0) ('不敌', '险胜')
(116.0, 103.0) ('不敌', '击败')
(107.0, 83.0) ('战胜', '轻取')
(127.0, 123.0) ('掀翻', '险胜')
(129.0, 133.0) ('轻取', '惜败')
(102.0, 69.0) ('不敌', '痛宰')
(128.0, 106.0) ('惜败', '轻取')
(121.0, 141.0) ('掀翻', '大败')
(102.0, 96.0) ('不敌', '掀翻')
(104.0, 91.0) ('险胜', '战胜')
(129.0, 107.0) ('击败', '轻取')
(115.0, 133.0) ('掀翻', '大败')
(101.0, 105.0) ('掀翻', '惜败')
(122.0, 98.0) ('掀翻', '轻取')
(123.0, 101.0) ('掀翻', '轻取')
(111.0, 129.0) ('掀翻', '大败')
(108.0, 117.0) ('战胜', '不敌')
(122.0, 125.0) ('惜败', '惜败')
(120.0, 99.0) ('不敌', '轻取')
(117.0, 114.0) ('惜败', '掀翻')
(127.0, 103.0) ('掀翻', '轻取')
(108.0, 96.0) ('惜败', '战胜')
(114.0, 92.0) ('险胜', '轻取')
(121.0, 99.0) ('不敌', '轻取')
(105.0, 123.0) ('惜败', '大败')
(115.0, 102.0) ('惜败', '击败')
(101.0, 97.0) ('掀翻', '险胜')
(107

...

4710 -0.211552 -0.496093 0.00176947
4720 -0.245248 -0.396388 0.00179018
4730 -0.182234 -0.598206 0.000602057
4740 -0.039702 -0.550631 0.00064849
4750 -0.0900119 -0.525672 0.000636968
4760 -0.145119 -0.685427 0.00119067
4770 -0.139169 -0.642052 0.000412562
4780 -0.0996665 -0.454054 0.00128939
4790 -0.0970105 -0.717565 0.000683798
4800 -0.225848 -0.53478 0.00163614
(124.0, 120.0) ('惜败', '掀翻')
(114.0, 110.0) ('险胜', '险胜')
(128.0, 133.0) ('不敌', '惜败')
(106.0, 74.0) ('痛宰', '痛宰')
(120.0, 116.0) ('险胜', '掀翻')
(102.0, 97.0) ('掀翻', '掀翻')
(103.0, 124.0) ('大败', '大败')
(109.0, 97.0) ('击败', '击败')
(106.0, 94.0) ('战胜', '战胜')
(123.0, 109.0) ('战胜', '击败')
(124.0, 118.0) ('险胜', '掀翻')
(126.0, 123.0) ('惜败', '险胜')
(104.0, 82.0) ('轻取', '轻取')
(101.0, 98.0) ('掀翻', '掀翻')
(109.0, 99.0) ('战胜', '战胜')
(112.0, 86.0) ('大胜', '大胜')
(100.0, 77.0) ('大胜', '轻取')
(103.0, 99.0) ('险胜', '掀翻')
(118.0, 105.0) ('击败', '击败')
(111.0, 85.0) ('大胜', '大胜')
(107.0, 101.0) ('掀翻', '掀翻')
(110.0, 119.0) ('不敌', '不敌')
(104.0, 72.0) ('痛宰', '痛宰')
(1

(110.0, 99.0) ('险胜', '战胜')
(101.0, 112.0) ('大败', '不敌')
(117.0, 103.0) ('击败', '击败')
(129.0, 149.0) ('大败', '大败')
(110.0, 82.0) ('大胜', '大胜')
(104.0, 78.0) ('轻取', '大胜')
(120.0, 110.0) ('险胜', '战胜')
(107.0, 104.0) ('掀翻', '掀翻')
(126.0, 100.0) ('大胜', '大胜')
(101.0, 91.0) ('险胜', '战胜')
(128.0, 148.0) ('大败', '大败')
(110.0, 112.0) ('惜败', '惜败')
(110.0, 112.0) ('惜败', '惜败')
(122.0, 117.0) ('险胜', '险胜')
(103.0, 121.0) ('大败', '大败')
(121.0, 141.0) ('大败', '大败')
(102.0, 123.0) ('大败', '大败')
(123.0, 90.0) ('痛宰', '痛宰')
(102.0, 110.0) ('不敌', '不敌')
(119.0, 108.0) ('战胜', '击败')
(107.0, 125.0) ('大败', '大败')
(106.0, 96.0) ('战胜', '战胜')
(101.0, 67.0) ('痛宰', '痛宰')
(103.0, 89.0) ('击败', '击败')
(104.0, 122.0) ('大败', '大败')
(105.0, 93.0) ('击败', '击败')
(104.0, 91.0) ('击败', '战胜')
(114.0, 102.0) ('击败', '战胜')
(113.0, 123.0) ('不敌', '不敌')
(125.0, 93.0) ('大胜', '痛宰')
(127.0, 115.0) ('掀翻', '击败')
(119.0, 98.0) ('轻取', '轻取')
(109.0, 129.0) ('大败', '大败')
(129.0, 97.0) ('大胜', '痛宰')
(116.0, 111.0) ('险胜', '掀翻')
(112.0, 88.0) ('轻取', '轻取')
(139.0

4810 -0.223466 -0.469368 0.00101968
4820 -0.103393 -0.765704 0.000380394
4830 -0.0193251 -0.624718 0.000977515
4840 -0.139605 -0.236076 0.00202468
4850 -0.156532 -0.537785 0.000575306
4860 -0.0750531 -0.628164 0.00102787
4870 -0.0752886 -0.582199 0.00155761
4880 -0.120609 -0.625982 0.000514526
4890 -0.241993 -0.52389 0.00106523
4900 -0.362799 -0.215334 0.00120659
(124.0, 120.0) ('险胜', '掀翻')
(114.0, 110.0) ('掀翻', '险胜')
(128.0, 133.0) ('不敌', '惜败')
(106.0, 74.0) ('痛宰', '痛宰')
(120.0, 116.0) ('险胜', '掀翻')
(102.0, 97.0) ('掀翻', '掀翻')
(103.0, 124.0) ('大败', '大败')
(109.0, 97.0) ('击败', '击败')
(106.0, 94.0) ('击败', '战胜')
(123.0, 109.0) ('击败', '击败')
(124.0, 118.0) ('险胜', '掀翻')
(126.0, 123.0) ('惜败', '险胜')
(104.0, 82.0) ('轻取', '轻取')
(101.0, 98.0) ('掀翻', '掀翻')
(109.0, 99.0) ('险胜', '战胜')
(112.0, 86.0) ('大胜', '大胜')
(100.0, 77.0) ('大胜', '轻取')
(103.0, 99.0) ('掀翻', '掀翻')
(118.0, 105.0) ('战胜', '击败')
(111.0, 85.0) ('大胜', '大胜')
(107.0, 101.0) ('险胜', '掀翻')
(110.0, 119.0) ('不敌', '不敌')
(104.0, 72.0) ('痛宰', '痛宰')
(1

(126.0, 144.0) ('大败', '大败')
(115.0, 105.0) ('险胜', '战胜')
(119.0, 93.0) ('轻取', '大胜')
(103.0, 91.0) ('击败', '战胜')
(111.0, 114.0) ('不敌', '惜败')
(121.0, 88.0) ('痛宰', '痛宰')
(101.0, 78.0) ('轻取', '轻取')
(106.0, 78.0) ('大胜', '大胜')
(124.0, 92.0) ('大胜', '痛宰')
(106.0, 85.0) ('轻取', '轻取')
(117.0, 89.0) ('轻取', '大胜')
(106.0, 95.0) ('战胜', '击败')
(119.0, 93.0) ('轻取', '大胜')
(122.0, 97.0) ('轻取', '大胜')
(121.0, 131.0) ('不敌', '不敌')
(114.0, 134.0) ('大败', '大败')
(112.0, 109.0) ('掀翻', '险胜')
(129.0, 116.0) ('战胜', '战胜')
(107.0, 85.0) ('轻取', '轻取')
(101.0, 67.0) ('痛宰', '痛宰')
(109.0, 103.0) ('险胜', '险胜')
(104.0, 77.0) ('大胜', '大胜')
(128.0, 100.0) ('大胜', '大胜')
(110.0, 115.0) ('不敌', '惜败')
(113.0, 80.0) ('痛宰', '痛宰')
(121.0, 108.0) ('击败', '战胜')
(102.0, 96.0) ('险胜', '掀翻')
(117.0, 119.0) ('惜败', '惜败')
(127.0, 114.0) ('战胜', '击败')
(109.0, 86.0) ('轻取', '轻取')
(116.0, 102.0) ('战胜', '击败')
(109.0, 104.0) ('掀翻', '掀翻')
(116.0, 82.0) ('大胜', '痛宰')
(117.0, 111.0) ('掀翻', '掀翻')
(124.0, 110.0) ('击败', '击败')
(102.0, 92.0) ('击败', '战胜')
(126.0, 123

4910 -0.156378 -0.645587 0.000514009
4920 -0.0538932 -0.598674 0.000420829
4930 -0.111931 -0.59612 0.00103202
4940 -0.151485 -0.56482 0.000402178
4950 -0.161525 -0.607038 0.000443037
4960 -0.0302218 -0.513643 0.0007008
4970 -0.106396 -0.561874 0.000768153
4980 -0.100645 -0.689585 0.00198383
4990 -0.178714 -0.480341 0.00110185


In [19]:
sess=tf.Session()   
sess.run(tf.global_variables_initializer())
saver = tf.train.import_meta_graph('trained_model-4500.meta')
saver.restore(sess,tf.train.latest_checkpoint('models/'))

INFO:tensorflow:Restoring parameters from ./trained_model-4500


In [20]:
def generate_samples():
        sc_gen, sc_disc, _data = get_next_batch(len(score_test), score_test, how_win_test, 0)
        samples = sess.run(sample_inputs, feed_dict={sample_size: len(sc_gen), score_for_gen:sc_gen, score_for_disc:sc_disc})
        samples = np.argmax(samples, axis=2)
        decoded_samples = []
        for i in range(len(samples)):
            decoded_samples.append((inv_charmap[samples[i][0]], inv_charmap[_data[i][0]]))
        return decoded_samples

下面两个情况说明模型学习到了不同比分下的单词，还是会出现本应“大胜”但是结果是“险胜”情况可能是因为训练次数不够，用的是训练了1500次的结果。

比分是负的情况在数据集里面只有4组，所以可能没学习出来。

下面的结果只出现了4种情况也应该是数据集分布不均匀，这四个词最多，所以其他词出现的概率很低。

In [23]:
#test one 
test_1_score = [(120, 60)]
#whatever
how_win_1 = ['大胜']
one_dict = {}
for i in range(100):
    sc_gen, sc_disc, _data = get_next_batch(len(test_1_score), test_1_score, how_win_1, 0)
    sample = sess.run(sample_inputs, feed_dict={sample_size: len(sc_gen), score_for_gen:sc_gen, score_for_disc:sc_disc})
    sample2 = np.argmax(sample, axis=2)
    hw = inv_charmap[sample2[0][0]]
    one_dict[hw] = one_dict[hw] + 1 if hw in one_dict else 1
"""
print(sc_disc[0][0][0], sc_disc[0][1][0])
print(sample[0][0])
print(sample2[0][0])
print(inv_charmap[sample2[0][0]])
inv_charmap
"""
one_dict

{'痛宰': 100}

In [24]:
#test one 
test_1_score = [(95, 100)]
#whatever
how_win_1 = ['惜败']
one_dict = {}
for i in range(100):
    sc_gen, sc_disc, _data = get_next_batch(len(test_1_score), test_1_score, how_win_1, 0)
    sample = sess.run(sample_inputs, feed_dict={sample_size: len(sc_gen), score_for_gen:sc_gen, score_for_disc:sc_disc})
    sample2 = np.argmax(sample, axis=2)
    hw = inv_charmap[sample2[0][0]]
    one_dict[hw] = one_dict[hw] + 1 if hw in one_dict else 1
"""
print(sc_disc[0][0][0], sc_disc[0][1][0])
print(sample[0][0])
print(sample2[0][0])
print(inv_charmap[sample2[0][0]])
inv_charmap
"""
one_dict

{'不敌': 56, '惜败': 43, '险胜': 1}